## A demo using Hydrogen Hamiltonian with GPT-QE.

In [1]:
import torch
from gqe.mingpt.utils import set_seed

set_seed(3407)

In [2]:
from qwrapper.operator import PauliObservable
from gqe.mingpt.cost import EnergyCost
from qswift.compiler import DefaultOperatorPool
from benchmark.molecule import DiatomicMolecularHamiltonian
from gqe.operator_pool.uccsd import UCCSD, do_generate_molecule
from gqe.common.initializer import HFStateInitializer
from gqe.util import get_device
from gqe.mingpt.callback import DefaultCallback, PrintMonitor, FileMonitor

# molecule = generate_molecule("Li", "H", 1.596, "sto-3g", bravyi_kitaev=False)
bond_length = 3.0
geometry = f"H 0.0 0.0 0.0\n" + f"Be 0.0 0.0 {bond_length}\n" + f"H 0.0 0.0 {2 * bond_length}\n"
molecule = do_generate_molecule(geometry, "sto-3g", bravyi_kitaev=False)
nqubit = 12

# prepare Hamiltonian
hamiltonian = DiatomicMolecularHamiltonian(nqubit, molecule, bravyi_kitaev=False)

# prepare operator_pool
uccsd = UCCSD(nqubit, molecule)
paulis = uccsd.paulis
paulis.append(PauliObservable("IIIIIIIIII"))
print('paulis', paulis)
num_operators = len(paulis)
initializer = HFStateInitializer(n_electrons=4)
pool = DefaultOperatorPool(paulis)
# time_pool = [1 / 320, -1 / 320, 1 / 160, -1 / 160, 1 / 80, -1 / 80, 1 / 40, -1 / 40, 0.05, -0.05, 0.1, -0.1, 0.2, -0.2]
time_pool = [1 / (2 ** j) for j in range(2, 12)]
time_pool.extend([-1 / (2 ** j) for j in range(2, 12)])

cost = EnergyCost(hamiltonian, initializer, pool, time_pool)


converged SCF energy = -15.0242100060364
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
skipped
paulis [+IIIYZXIIIIII, +IIIYZZZXIIII, +IIIYZZZZZXII, +IIIYZZZZZZZX, +IIXXIIIIIIYX, +IIXXIIIIYXII, +IIXXIIYXIIII, +IIXXYXIIIIII,

## FCI energy by diagonalization

In [3]:
from qwrapper.hamiltonian import compute_ground_state

#print(compute_ground_state(hamiltonian))

In [4]:
print("hf state:", hamiltonian.exact_value(initializer.init_circuit(12, [], "qulacs")))

hf state: -15.024210006036476


## Setup for GPT

In [5]:
# create a GPT instance
from gqe.mingpt.model import GPT

num_layers = 10



In [6]:
# create a Trainer object
from gqe.mingpt.trainer import Trainer
from gqe.mingpt.layer import LayerWiseFineTuneTrainer, LayerWiseFactory
from qwrapper.optimizer import AdamOptimizer
from math import pi

pool = DefaultOperatorPool(paulis)

# time_pool = [1 / 320, -1 / 320, 1 / 160, -1 / 160, 1 / 80, -1 / 80, 1 / 40, -1 / 40, 0.05, -0.05, 0.1, -0.1, 0.2, -0.2]

# time_pool = [pi * j / 30 for j in range(0, 30)]
# time_pool.extend([-pi * j / 30 for j in range(0, 30)])

import math

time_pool = [math.pi / 2 ** j for j in range(3, 8)]
time_pool.extend([-math.pi / 2 ** j for j in range(3, 8)])


class CustomFactory(LayerWiseFactory):
    def generate_train_config(self, layer):
        train_config = Trainer.get_default_config()
        train_config.learning_rate = 5e-7  # the model we're using is so small that we can go a bit faster
        train_config.max_iters = 500
        train_config.num_workers = 5
        train_config.n_samples = 50
        return train_config

    def generate_model_config(self, layer):
        model_config = GPT.get_default_config()
        model_config.model_type = 'gpt2-medium'
        model_config.vocab_size = pool.size() * len(time_pool)
        model_config.n_gates = 10  # The number of gates for each circuit
        model_config.block_size = model_config.n_gates
        model_config.temperature = 5  # Each gate is generated with probability exp(-temperature * logit)
        model_config.embd_pdrop = 0
        model_config.resid_pdrop = 0
        model_config.attn_pdrop = 0
        model_config.std = 0.02
        model_config.energy_offset = 14
        return model_config


trainer = LayerWiseFineTuneTrainer(CustomFactory(),
                                   hamiltonian=hamiltonian,
                                   initializer=initializer, optimizer=AdamOptimizer(maxiter=300),
                                   num_layers=num_layers, device=get_device(), pool=pool, taus=time_pool)

In [7]:
print_monitors = []
file_monitors = []
for index in range(num_layers):
    file_monitor = FileMonitor()
    file_monitors.append(file_monitor)
    trainer.set_monitors(index, [PrintMonitor(), file_monitor])
trainer.run()
#torch.save(model.state_dict(), '../saved_models/gptqe_test_2')

layer: 1 starts running
number of parameters: 303.11M
running on device mps
iter_dt 0.00s; iter 0: train loss 9.42424 temperature: 5
mean_logits tensor([-15.4771, -15.7391, -15.7587, -15.7707, -15.7478, -15.7487, -15.4394,
        -15.6712, -15.9507, -15.6997, -15.6936, -15.5454, -15.4871, -15.7036,
        -15.7228, -15.6668, -15.8136, -15.6989, -15.7532, -15.5186, -15.7783,
        -15.5454, -15.5489, -15.3425, -15.7031, -15.6520, -15.4957, -15.5523,
        -15.3559, -15.4944, -15.7751, -15.5172, -15.5022, -15.5502, -15.6407,
        -16.0303, -15.6909, -15.3942, -15.9577, -15.8705, -15.5146, -15.7293,
        -15.4325, -15.3919, -15.5696, -15.7493, -15.6076, -15.3990, -15.6428,
        -15.7689], device='mps:0', grad_fn=<SubBackward0>)
energies: tensor([-14.9141, -14.5084, -14.8391, -14.9172, -14.8717, -14.8791, -14.8628,
        -14.8477, -14.7380, -14.7551, -14.8331, -14.9228, -15.0172, -14.8434,
        -14.8238, -14.9163, -14.8622, -14.8135, -14.6203, -14.9104, -14.8608,
      

In [8]:
indices = []
for fm in file_monitors:
    print(fm.min_energy)
    indices.extend(fm.min_indices)
print(trainer.vqe.value())

-15.2798490524292
-15.28887939453125
-15.298073768615723
-15.303869247436523
-15.30505084991455
-15.30907917022705
-15.314248085021973
-15.318799018859863
-15.320525169372559
-15.323375701904297
-15.326906664978853
